## Gradio Pets

Since the `learn.fine_tune(3)` took very long time in local machine, running it in Kaggle.

- Hugging Face - Org Source: https://huggingface.co/spaces/prasanthntu/pets/blob/main/train.ipynb
- Kaggle link: https://www.kaggle.com/prasanth07/fastai-prd-apps-pets-training

Part of `fastai-course22` > Lesson 3: https://github.com/prasanth-ntu/fastai-course22/blob/master/kaggle_version/03-which-image-models-are-best.ipynb

In [1]:
from fastai.vision.all import *
import timm
import os, sys
import numpy as np
import pandas as pd

In [2]:
path = untar_data(URLs.PETS)/'images'

dls = ImageDataLoaders.from_name_func('.',
    get_image_files(path), valid_pct=0.2, seed=42,
    # Regex captures the part of the filename before the underscore followed by decimal values, 
    # which typically represents the class of the image (e.g., basset_hound_112.jpg > basset_bound)
    label_func=RegexLabeller(pat = r'^([^/]+)_\d+'), 
    item_tfms=Resize(224))

In [19]:
print(f"path: {path}")

# List the contents of the directory
files = os.listdir(path)
print (f"sample files: {files[:5]}")
labels = [file.split('_')[0] for file in files]
labels_unique = np.unique(labels)
print (f"No. of unique pet types: {len(labels_unique)}")
print (f"Sample pet types: {list(labels_unique[:5])}")

path: /Users/prasanth.thangavel/.fastai/data/oxford-iiit-pet/images
sample files: ['Egyptian_Mau_167.jpg', 'pug_52.jpg', 'basset_hound_112.jpg', 'Siamese_193.jpg', 'shiba_inu_122.jpg']
No. of unique pet types: 35
Sample pet types: ['Abyssinian', 'Bengal', 'Birman', 'Bombay', 'British']


In [ ]:
dls.show_batch(max_n=4)

In [4]:
learn = vision_learner(dls, resnet34, metrics=error_rate)
learn.fine_tune(3)

/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet34_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet34_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet34-b627a593.pth" to /root/.cache/torch/hub/checkpoints/resnet34-b627a593.pth
100%|██████████| 83.3M/83.3M [00:00<00:00, 102MB/s] 


We could try a better model, based on [this analysis](https://www.kaggle.com/code/jhoward/which-image-models-are-best/). The convnext models work great!

In [5]:
timm.list_models('convnext*')

['convnext_atto',
 'convnext_atto_ols',
 'convnext_base',
 'convnext_femto',
 'convnext_femto_ols',
 'convnext_large',
 'convnext_large_mlp',
 'convnext_nano',
 'convnext_nano_ols',
 'convnext_pico',
 'convnext_pico_ols',
 'convnext_small',
 'convnext_tiny',
 'convnext_tiny_hnf',
 'convnext_xlarge',
 'convnext_xxlarge',
 'convnextv2_atto',
 'convnextv2_base',
 'convnextv2_femto',
 'convnextv2_huge',
 'convnextv2_large',
 'convnextv2_nano',
 'convnextv2_pico',
 'convnextv2_small',
 'convnextv2_tiny']

In [6]:
learn = vision_learner(dls, 'convnext_tiny_in22k', metrics=error_rate).to_fp16()
learn.fine_tune(3)

/opt/conda/lib/python3.10/site-packages/timm/models/_factory.py:114: UserWarning: Mapping deprecated model name convnext_tiny_in22k to current convnext_tiny.fb_in22k.
  model = create_fn(


In [7]:
learn.export('model.pkl')

In [10]:
!pwd

/kaggle/working


In [11]:
!ls

__notebook_source__.ipynb  model.pkl


<a href="model.pkl"> Download model.pkl File </a>
